In [1]:
from pycbc.waveform import get_fd_waveform, get_td_waveform
from pycbc.filter import sigma,sigmasq
import pycbc.conversions as conversions
import pycbc.psd
from pycbc.detector import Detector
import matplotlib.pyplot as plt

In [2]:
import h5py,numpy as np
f = h5py.File('./injection.hdf')

In [3]:
for k in f.keys():
    print(k,f[k][:])

coa_phase [5.36965906e+00 5.07592564e+00 4.36050028e+00 6.23246784e+00
 5.27833413e+00 8.06530320e-01 2.21489867e+00 5.54512520e+00
 6.58695514e-01 4.96770779e+00 3.84762007e+00 3.32413202e+00
 2.42012515e+00 2.27417365e+00 3.23394967e+00 1.25609794e+00
 6.11123758e+00 2.56977798e+00 3.70874075e+00 4.71327539e+00
 3.39948997e+00 6.39930773e-01 6.00435114e+00 1.08937480e+00
 1.70347051e+00 4.01220917e+00 2.53072909e+00 3.30253315e+00
 1.51650137e+00 5.01462590e-01 2.98872260e+00 4.21589102e+00
 3.76383772e-03 5.62107133e+00 5.83593299e+00 5.48946475e+00
 3.45022393e+00 4.67195899e+00 1.18391533e+00 5.57102646e-01
 9.55556113e-01 3.77127876e-01 1.02951127e-01 3.25265491e+00
 5.36519872e+00 6.12445206e+00 5.80591680e-01 3.90479680e+00
 2.20884098e+00 5.71148173e+00 3.70938987e+00 5.97381039e+00
 2.91851622e+00 5.20935776e+00 1.83034358e+00 3.44659796e+00
 1.39646231e+00 2.62939625e+00 5.77087617e+00 3.28341333e+00
 1.92183981e+00 2.40500914e+00 5.00061740e+00 2.36643863e+00
 3.77309348e+0

In [4]:
np.max(f['distance']),np.min(f['distance'])

(44203.81893477349, 3367.6957367915707)

In [5]:
snrs = {}
detector_signals = {}
psds = {}
total_snr = []

for i in range(np.size(f['mass1'][()])):
    print('i:',i)
    for det in ('H1', 'L1','V1'):
        # 1. estimating PSDs
        delta_f = 1.0 / 8
        flen = int(1024 / delta_f) + 1
        low_frequency_cutoff = 20
        if det != 'V1':
            psds[det] = pycbc.psd.aLIGOZeroDetHighPower(flen, delta_f, low_frequency_cutoff)
        else:
            psds[det] = pycbc.psd.AdvVirgo(flen, delta_f, low_frequency_cutoff)
        # 2. detector_signals
        hp,hc =  get_fd_waveform(approximant='IMRPhenomPv2',
                             mass1=f['mass1'][i],
                             mass2=f['mass2'][i],
                             spin1x=f['spin1x'][i],
                             spin1y=f['spin1y'][i],
                             spin1z=f['spin1z'][i],
                             spin2x=f['spin2x'][i],
                             spin2y=f['spin2y'][i],
                             spin2z=f['spin2z'][i],
                             distance=f['distance'][i],
                             inclination=f['inclination'][i],
                             coa_phase=f['coa_phase'][i],
                             delta_f=delta_f,
                             f_lower=low_frequency_cutoff)
        class_det = Detector(det)        
        fp, fc = class_det.antenna_pattern(f['ra'][i],f['dec'][i],f['polarization'][i],f.attrs['tc'])
        detector_signals[det] = fp*hp + fc*hc
        # 3. compute the SNR
        snrs[det] = sigma(htilde=detector_signals[det],psd=psds[det],low_frequency_cutoff=low_frequency_cutoff,
                         high_frequency_cutoff=1024)
        print('snrs',det,snrs[det])
    total_snr.append(np.sqrt(snrs['H1']**2 + snrs['L1']**2 + snrs['V1']**2))

i: 0
snrs H1 1.2216084288002764
snrs L1 0.4635167615098742
snrs V1 1.1097750081379556
i: 1
snrs H1 0.8410189563791978
snrs L1 0.5416977331212025
snrs V1 1.3921300913155623
i: 2
snrs H1 1.2362523765953919
snrs L1 0.807799623086722
snrs V1 0.8705833334651405
i: 3
snrs H1 0.8944898322014365
snrs L1 1.1245668514790965
snrs V1 0.9348865422321146
i: 4
snrs H1 1.0734189603153315
snrs L1 1.1844468077494452
snrs V1 0.6193811471555976
i: 5
snrs H1 1.3402077645393917
snrs L1 1.057447017078462
snrs V1 0.156283281717112
i: 6
snrs H1 0.9068300203095435
snrs L1 1.3837882329398539
snrs V1 0.4489598543819613
i: 7
snrs H1 1.070187087405006
snrs L1 1.2062975265898985
snrs V1 0.5816540084094359
i: 8
snrs H1 1.0672703055396129
snrs L1 1.2666219213280066
snrs V1 0.4420164177141073
i: 9
snrs H1 0.8750526856580617
snrs L1 1.138076112734054
snrs V1 0.9369317313181575
i: 10
snrs H1 0.42002622918059407
snrs L1 0.6161810583037023
snrs V1 1.5435913903595544
i: 11
snrs H1 1.0820427864770021
snrs L1 1.21502923727882

snrs H1 1.2037800425741534
snrs L1 1.0693422352247228
snrs V1 0.5883844859178772


In [6]:
total_snr

[1.7142857142857142,
 1.714285714285714,
 1.7142857142857142,
 1.7142857142857144,
 1.7142857142857144,
 1.7142857142857142,
 1.7142857142857144,
 1.714285714285714,
 1.7142857142857142,
 1.7142857142857144,
 1.7142857142857144,
 1.7142857142857146,
 1.714285714285714,
 1.7142857142857144,
 1.7142857142857137,
 1.714285714285714,
 1.7142857142857146,
 1.7142857142857149,
 1.714285714285714,
 1.7142857142857142,
 1.7142857142857146,
 1.7142857142857144,
 1.714285714285714,
 1.714285714285714,
 1.7142857142857142,
 1.714285714285714,
 1.7142857142857142,
 1.7142857142857144,
 1.7142857142857142,
 1.714285714285714,
 1.7142857142857142,
 1.714285714285714,
 1.7142857142857142,
 1.7142857142857146,
 1.7142857142857144,
 1.714285714285714,
 1.7142857142857146,
 1.7142857142857144,
 1.714285714285714,
 1.7142857142857144,
 1.714285714285714,
 1.7142857142857144,
 1.7142857142857142,
 1.7142857142857137,
 1.7142857142857144,
 1.7142857142857144,
 1.7142857142857135,
 1.7142857142857144,
 1.71

In [7]:
new_snr = 8
new_distance = f['distance'][()] * total_snr / new_snr

In [8]:
new_distance

array([3667.27177101, 1165.33912425, 2554.5024557 , 4044.51460328,
       5387.51474473, 5914.41357078, 1064.53793679, 1584.01974041,
       3538.87858708, 4910.30203758, 3730.88854045, 2070.16351682,
       3344.83042257, 2986.28578836, 3445.82165921, 3447.18340402,
       3003.63697191, 7680.93435931, 1517.03894558, 1630.92715739,
       4890.96285483, 1850.55990509, 2764.75081081, 7328.46064824,
       3181.56270536, 5155.40821205, 3002.51113127, 3377.87147035,
        721.64908646, 2960.48984028, 1611.27167628, 7680.72535388,
       1552.96112908, 4577.60796118, 6628.39288552, 4938.14531072,
       2256.065849  , 2120.69172916, 1104.04376633, 1480.13786271,
       3041.0758985 , 1844.25222585, 4059.00711435, 1803.21075032,
       5235.61105249, 4659.20466792, 2227.30035015, 1700.8486659 ,
       1742.64638619, 2623.03345819, 2728.03668278, 2240.51569794,
       2634.10773316, 4724.80115556, 2676.59005886, 2131.42670977,
       2047.4949448 , 5236.51545661, 1356.45165241, 9472.24691

In [9]:
f['distance'][:]

array([17113.93493138,  5438.2492465 , 11921.01145993, 18874.40148199,
       25141.7354754 , 27600.59666364,  4967.843705  ,  7392.0921219 ,
       16514.76673969, 22914.74284205, 17410.81318874,  9660.7630785 ,
       15609.20863868, 13936.00034566, 16080.50107632, 16086.85588543,
       14016.97253558, 35844.36034343,  7079.5150794 ,  7610.99340115,
       22824.49332256,  8635.94622376, 12902.17045046, 34199.48302511,
       14847.29262501, 24058.57165625, 14011.7186126 , 15763.40019496,
        3367.69573679, 13815.61925465,  7519.26782262, 35843.38498477,
        7247.15193572, 21362.17048551, 30932.50013242, 23044.67811669,
       10528.30729531,  9896.56140276,  5152.20424289,  6907.310026  ,
       14191.68752632,  8606.51038729, 18942.03320029,  8414.98350152,
       24432.85157828, 21742.95511694, 10394.06830072,  7937.29377421,
        8132.34980223, 12240.82280487, 12730.83785298, 10455.73992373,
       12292.50275475, 22049.07205928, 12490.75360803,  9946.65797892,
      

In [10]:
f.close()

In [11]:
a = h5py.File('./injection.hdf','r+')
a['distance'][:] = new_distance
a.close()